# Introduction

In order to train on the words in a legislative bill we want to make use of an existing Natural Language Processing (NLP) model in order to come up with a data structure that will encode contextual information.

To this end we use the BERT model, which is one of the modern NLP models that takes into account context.

For this project, we want to take the text from the bill and predict which party sponsored it

## First steps

Load the BERT model using pytorch.

Why pytorch, this is higher level libary for constructing machine learning models.

In [1]:
import fnmatch
import os.path

import pandas as pd
import transformers
from transformers import pipeline
import pandas as pd
import torch
import numpy as np
import json

In [2]:
from transformers import BertTokenizer, BertModel
tokenizer = BertTokenizer.from_pretrained('bert-base-cased')
model = BertModel.from_pretrained("bert-base-cased")

Some weights of the model checkpoint at bert-base-cased were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.dense.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


Now that we have the model, we want to run inference on the text and get the output token.

In [3]:
def generate_token(summary_json):
    """
    execute the BERT model on the title section of the summary
    :param summary_json: the data from a summary file
    :return: a numpy vector
    """
    text = summary_json['text']
    encoded_input = tokenizer(text, return_tensors='pt')
    print("encoded input")
    print(encoded_input)
    print("model output")
    output = model(**encoded_input)
#    print(type(output))
    last_shape = output.last_hidden_state.shape
    elements = np.cumproduct(last_shape)
    last_layer_vector = torch.from_numpy(output.last_hidden_state.detach().numpy().reshape(max(elements)))
#    print(type(last_layer_vector))
    return last_layer_vector

In [4]:
parent_path = os.path.dirname(os.getcwd())
search_path = os.path.join(parent_path, "data", "extracted")
token_path = os.path.join(parent_path, "data", "tokenized")

In [11]:
import pickle
for root, dirs, files in os.walk(search_path):
    for f in files:
        with open(os.path.join(root, f), 'r') as s_file:
            print(f'reading {f}')
            try:
                summary = json.load(s_file)
                encoding = generate_token(summary)
                print(f'{len(encoding)} of type {type(encoding)}')
                summary["input_full"] = encoding
                df = pd.DataFrame(summary)
                output_path = os.path.join(token_path, f.replace(".json",".pkl"))
                print(f'saving {output_path}')
                df.to_pickle(output_path,compression="gzip",protocol=pickle.DEFAULT_PROTOCOL)
            except json.JSONDecodeError:
                with open("json_error.txt", 'a') as err_file:
                    err_file.write(s_file.name+"\n")
            except:
                with open("general_error.txt", 'a') as err_file:
                    err_file.write(s_file.name+"\n")




reading summary_bill_1811_1392983.json
encoded input
{'input_ids': tensor([[  101,   142,  8419,  1830, 27706,  8826,  1111,  5186,  2989,  8132,
           118, 18572,  1104,  6538,  2308,   119,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]])}
model output
13056 of type <class 'torch.Tensor'>
saving C:\Users\benja\git-projects\bitbucket\nlp_legislation_prediction\data\tokenized\summary_bill_1811_1392983.pkl
reading summary_bill_1811_1392984.json
encoded input
{'input_ids': tensor([[  101, 11336, 26304,  1106,  1103,  5991,  4412,  1104, 14689,  1111,
          2436,   119,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]])}
model output
9984 of type <class 'torch.Tensor'>
saving C:\Users\benja\git-projects\bitbucket\nlp_legislation_prediction\data\tokenized\summary_bil

These tensors all have different sizes, so running a cosine similarity will not work.
I will try to compress these down to a standard size.
Let's try this  : https://newbedev.com/downsample-a-1d-numpy-array

Let's reload and the dfs and save a resampled version of the encoding

In [12]:
import numpy as np
from scipy.signal import resample
from scipy.interpolate import interp1d

def ResampleLinear1D(original, targetLen):
    original = np.array(original, dtype=np.float)

    index_arr = np.linspace(0, len(original)-1, num=targetLen, dtype=np.float)
    index_floor = np.array(index_arr, dtype=np.int) #Round down

    index_ceil = index_floor + 1
    index_rem = index_arr - index_floor #Remain

    val1 = original[index_floor]
    val2 = original[index_ceil % len(original)]
    interp = val1 * (1.0-index_rem) + val2 * index_rem
    assert(len(interp) == targetLen)
    return interp

In [13]:
print(f'tokenized files are in {token_path}')
import fnmatch
for root,dirs, files in os.walk(token_path):
    for f in files:
        if not fnmatch.fnmatch(f, "*shrunk*"):
            pkl_file_path = os.path.join(root, f)
            print(f"processsing {f}")
            df = pd.read_pickle(pkl_file_path, compression="gzip")
    #        print(df)
            shrunk = ResampleLinear1D(df["input_full"], 2048)
    #        print(shrunk)
            # "status": 2, "party": 1
            df2 = pd.DataFrame({"status": df["status"][0:2048],
                                "party": df["party"][0:2048],
                                "input_shrunk": shrunk})
    #        print(df2.shape)
            df2.to_pickle(pkl_file_path.replace(".pkl","-shrunk.pkl"),compression="gzip", protocol=pickle.DEFAULT_PROTOCOL)

tokenized files are in C:\Users\benja\git-projects\bitbucket\nlp_legislation_prediction\data\tokenized
processsing summary_bill_1811_1392983.pkl
processsing summary_bill_1811_1392984.pkl
processsing summary_bill_1811_1392985.pkl
processsing summary_bill_1811_1392986.pkl
processsing summary_bill_1811_1392988.pkl
processsing summary_bill_1811_1392989.pkl
processsing summary_bill_1811_1392990.pkl
processsing summary_bill_1811_1392991.pkl
processsing summary_bill_1811_1392992.pkl
processsing summary_bill_1811_1392994.pkl
processsing summary_bill_1811_1392995.pkl
processsing summary_bill_1811_1392996.pkl


C:\Users\benja\AppData\Local\Temp\ipykernel_22960\376862322.py:6: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  original = np.array(original, dtype=np.float)
C:\Users\benja\AppData\Local\Temp\ipykernel_22960\376862322.py:8: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  index_arr = np.linspace(0, len(original)-1, num=targetLen, dtype=np.fl

processsing summary_bill_1811_1392997.pkl
processsing summary_bill_1811_1393000.pkl
processsing summary_bill_1811_1393001.pkl
processsing summary_bill_1811_1393002.pkl
processsing summary_bill_1811_1393003.pkl
processsing summary_bill_1811_1393005.pkl
processsing summary_bill_1811_1393007.pkl
processsing summary_bill_1811_1393008.pkl
processsing summary_bill_1811_1393009.pkl
processsing summary_bill_1811_1393010.pkl
processsing summary_bill_1811_1393011.pkl
processsing summary_bill_1811_1393013.pkl


C:\Users\benja\AppData\Local\Temp\ipykernel_22960\376862322.py:6: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  original = np.array(original, dtype=np.float)
C:\Users\benja\AppData\Local\Temp\ipykernel_22960\376862322.py:8: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  index_arr = np.linspace(0, len(original)-1, num=targetLen, dtype=np.fl

processsing summary_bill_1811_1393014.pkl
processsing summary_bill_1811_1393015.pkl
processsing summary_bill_1811_1393017.pkl
processsing summary_bill_1811_1393019.pkl
processsing summary_bill_1811_1393020.pkl
processsing summary_bill_1811_1393021.pkl
processsing summary_bill_1811_1393022.pkl
processsing summary_bill_1811_1393023.pkl
processsing summary_bill_1811_1393024.pkl
processsing summary_bill_1811_1393026.pkl
processsing summary_bill_1811_1393028.pkl


...

C:\Users\benja\AppData\Local\Temp\ipykernel_22960\376862322.py:6: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  original = np.array(original, dtype=np.float)
C:\Users\benja\AppData\Local\Temp\ipykernel_22960\376862322.py:8: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  index_arr = np.linspace(0, len(original)-1, num=targetLen, dtype=np.fl

processsing summary_bill_1959_1546393.pkl
processsing summary_bill_1959_1546395.pkl
processsing summary_bill_1959_1546399.pkl
processsing summary_bill_1959_1546402.pkl
processsing summary_bill_1959_1546404.pkl
processsing summary_bill_1959_1546408.pkl
processsing summary_bill_1959_1546412.pkl
processsing summary_bill_1959_1546414.pkl
processsing summary_bill_1959_1546417.pkl
processsing summary_bill_1959_1546421.pkl
processsing summary_bill_1959_1546423.pkl
processsing summary_bill_1959_1546427.pkl
processsing summary_bill_1959_1546429.pkl
processsing summary_bill_1959_1546431.pkl
processsing summary_bill_1959_1546435.pkl
processsing summary_bill_1959_1546438.pkl
processsing summary_bill_1959_1546440.pkl
processsing summary_bill_1959_1546443.pkl
processsing summary_bill_1959_1546445.pkl
processsing summary_bill_1959_1546448.pkl
processsing summary_bill_1959_1546451.pkl
processsing summary_bill_1959_1546454.pkl
processsing summary_bill_1959_1546457.pkl
processsing summary_bill_1959_1546

C:\Users\benja\AppData\Local\Temp\ipykernel_22960\376862322.py:6: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  original = np.array(original, dtype=np.float)
C:\Users\benja\AppData\Local\Temp\ipykernel_22960\376862322.py:8: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  index_arr = np.linspace(0, len(original)-1, num=targetLen, dtype=np.fl

processsing summary_bill_1959_1546466.pkl
processsing summary_bill_1959_1546468.pkl
processsing summary_bill_1959_1546469.pkl
processsing summary_bill_1959_1546471.pkl
processsing summary_bill_1959_1575848.pkl
processsing summary_bill_1959_1579738.pkl
processsing summary_bill_1959_1579816.pkl
processsing summary_bill_1959_1579892.pkl
processsing summary_bill_1959_1579963.pkl
processsing summary_bill_1959_1583495.pkl
processsing summary_bill_1959_1595686.pkl
processsing summary_bill_1959_1599982.pkl
processsing summary_bill_1959_1607568.pkl
processsing summary_bill_1959_1615421.pkl
processsing summary_bill_1959_1616153.pkl
processsing summary_bill_1959_1616154.pkl


C:\Users\benja\AppData\Local\Temp\ipykernel_22960\376862322.py:6: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  original = np.array(original, dtype=np.float)
C:\Users\benja\AppData\Local\Temp\ipykernel_22960\376862322.py:8: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  index_arr = np.linspace(0, len(original)-1, num=targetLen, dtype=np.fl

Doing the interpolation, while convienent, may be supressing important information. Let's try using max pooling instead.
This to get a consisent on the output, we need to pad the token vector so that we have a multiple of 2048 elements.

In [17]:
import math
def max_pool_to_size(encoding: torch.Tensor, target_size):
    """
    Take the raw bert encoding and use max pool 1d to get to the target size,
    will need to pad the encoding.
    MaxPool1D takes in two variables that control how the max-pooling works, stride and kernel size. For simpliclity we will
    take stride to equal kernel size.
    :param encoding: the raw bert encoding
    :param target_size: the number of elements in the output vector
    :return:
    """

    enc_length = len(encoding)
    print(enc_length)
    if enc_length % target_size == 0:
        kernel_size = int(enc_length / target_size)
        padding = 0

    else:
        kernel_size = math.floor(enc_length / target_size) + 1
        padding = (kernel_size * target_size) - enc_length

    if padding == 0:
        mp_tensor = encoding
        padded_size = enc_length
    elif padding < 0:
        print(f"oops. got padding {padding} for kernel_size {kernel_size}, enc_length {enc_length}")
        raise ValueError("oops")
    else:
        # concatenate on an tensor of zeros to the end to
        mp_tensor = torch.cat((encoding, torch.Tensor(np.zeros(padding))))
        padded_size = len(mp_tensor)
    # print(f'original length {enc_length}, padding {padding}, padded size {padded_size}, kernel = {kernel_size}')
    maxpooler = torch.nn.MaxPool1d(kernel_size, stride=kernel_size, padding=0)
    return maxpooler(mp_tensor.resize(1,padded_size))


In [74]:
for root,dirs, files in os.walk(token_path):
    for f in files:
        if not fnmatch.fnmatch(f, "*shrunk*") and not fnmatch.fnmatch(f, "*maxpool*"):
            pkl_file_path = os.path.join(root, f)
            print(f"processsing {f}")
            df = pd.read_pickle(pkl_file_path, compression="gzip")
            shrunk = max_pool_to_size(torch.Tensor(df["input_full"]), 2048)
            # "status": 2, "party": 1
            df2 = pd.DataFrame({"status": df["status"][0:2048],
                                "party": df["party"][0:2048],
                                "input_maxpool": shrunk.reshape(2048)})
    #        print(df2.shape)
            df2.to_pickle(pkl_file_path.replace(".pkl","-maxpool.pkl"),compression="gzip", protocol=pickle.DEFAULT_PROTOCOL)

processsing summary_bill_1811_1392983.pkl
13056
tensor([0.2109, 0.2171, 0.2904,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1392984.pkl
9984
tensor([0.0900, 0.2322, 0.1415,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1392985.pkl
16128
tensor([0.2159, 0.1174, 0.6138,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1392986.pkl
11520
tensor([0.1158, 0.2333, 0.4173,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1392988.pkl
14592
tensor([0.3300, 0.2444, 0.4580,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1392989.pkl
16896
tensor([0.5314, 0.3231, 0.6546,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1392990.pkl
11520
tensor([0.1683, 0.2834, 0.3899,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1392991.pkl
10752
tensor([0.0542, 0.4666, 0.3538,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1392992.pkl
9984
tensor([0.0225, 0.2613, 0.2645,  ..., 0.0000, 0.0000, 0.0000])
pro

c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  

tensor([0.2768, 0.1267, 0.3274,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1393005.pkl
5376
tensor([0.2031, 0.0096, 0.5237,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1393007.pkl
10752
tensor([0.1749, 0.2095, 0.5359,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1393008.pkl
9216
tensor([0.3018, 0.2343, 0.1469,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1393009.pkl
13056
tensor([0.3497, 0.2065, 0.3542,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1393010.pkl
16128
tensor([0.3645, 0.1123, 0.7532,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1393011.pkl
7680
tensor([0.2144, 0.6070, 0.2150,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1393013.pkl
9216
tensor([0.4335, 0.3267, 0.0389,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1393014.pkl
11520
tensor([0.2328, 0.2471, 0.4453,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1393015.pkl
7680
tensor

c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  

15360
tensor([0.3358, 0.2551, 0.6558,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1393030.pkl
9984
tensor([0.1472, 0.1875, 0.1243,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1393032.pkl
8448
tensor([0.3052, 0.2592, 0.1978,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1393033.pkl
16128
tensor([0.2219, 0.1265, 0.6674,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1393034.pkl
9984
tensor([0.1065, 0.2386, 0.1989,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1393036.pkl
8448
tensor([0.1275, 0.3325, 0.1489,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1393038.pkl
13824
tensor([0.2121, 0.1616, 0.3055,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1393039.pkl
9984
tensor([0.0010, 0.1949, 0.2118,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1393040.pkl
8448
tensor([0.2235, 0.4749, 0.1461,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1811_1393041.pkl
11520
t

...

c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  

13056
tensor([0.2115, 0.0490, 0.2576,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1959_1546451.pkl
23040
tensor([0.3408, 0.4891, 0.1881,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1959_1546454.pkl
11520
tensor([0.0886, 0.3471, 0.2621,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1959_1546457.pkl
9984
tensor([-0.0436,  0.4010,  0.2008,  ...,  0.0000,  0.0000,  0.0000])
processsing summary_bill_1959_1546461.pkl
9216
tensor([0.1940, 0.2799, 0.2220,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1959_1546463.pkl
21504
tensor([0.2501, 0.1644, 0.7338,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1959_1546466.pkl
12288
tensor([-0.0285,  0.2516,  0.2685,  ...,  1.0141,  0.6786,  0.3453])
processsing summary_bill_1959_1546468.pkl
10752
tensor([0.1615, 0.3873, 0.3773,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1959_1546469.pkl
13824
tensor([0.1636, 0.1571, 0.1668,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1959_154

c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  

processsing summary_bill_1959_1583495.pkl
6912
tensor([0.2688, 0.2325, 0.3955,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1959_1595686.pkl
10752
tensor([0.2072, 0.2989, 0.2659,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1959_1599982.pkl
13824
tensor([0.4423, 0.1596, 0.4532,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1959_1607568.pkl
6912
tensor([-0.0119,  0.4272,  0.0291,  ...,  0.0000,  0.0000,  0.0000])
processsing summary_bill_1959_1615421.pkl
7680
tensor([0.2711, 0.1491, 0.4071,  ..., 0.0000, 0.0000, 0.0000])
processsing summary_bill_1959_1616153.pkl
6144
tensor([0.1350, 0.5342, 0.5220,  ..., 1.4173, 0.5085, 0.6908])
processsing summary_bill_1959_1616154.pkl
4608
tensor([ 0.1358, -0.0170,  0.1205,  ...,  0.0000,  0.0000,  0.0000])


c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\benja\git-projects\bitbucket\nlp_legislation_prediction\venvs3\lib\site-packages\torch\_tensor.py:493: UserWarning: non-inplace resize is deprecated
  

In [19]:
import pickle
for root,dirs, files in os.walk(token_path):
    for f in files:
        target_size = 512
        if not fnmatch.fnmatch(f, "*shrunk*") and not fnmatch.fnmatch(f, "*maxpool*") and not fnmatch.fnmatch(f, '*.tar.gz'):
            pkl_file_path = os.path.join(root, f)
            print(f"processsing {f}")
            df = pd.read_pickle(pkl_file_path, compression="gzip")
            shrunk = max_pool_to_size(torch.Tensor(df["input_full"]), target_size)
            # "status": 2, "party": 1
            df2 = pd.DataFrame({"status": df["status"][0:target_size],
                                "party": df["party"][0:target_size],
                                "input_maxpool": shrunk.reshape(target_size)})
    #        print(df2.shape)
            df2.to_pickle(pkl_file_path.replace(".pkl","-maxpool-512.pkl"),compression="gzip", protocol=pickle.DEFAULT_PROTOCOL)

processsing summary_bill_1811_1407132.pkl
9984
processsing summary_bill_1811_1405761.pkl
16896
processsing summary_bill_1811_1396361.pkl
16128
processsing summary_bill_1811_1393208.pkl
8448
processsing summary_bill_1959_1543005.pkl
15360
processsing summary_bill_1959_1543351.pkl
25344
processsing summary_bill_1811_1393093.pkl
16128
processsing summary_bill_1811_1435240.pkl
10752
processsing summary_bill_1959_1545940.pkl
13056
processsing summary_bill_1811_1403860.pkl
21504
processsing summary_bill_1811_1396364.pkl
8448
processsing summary_bill_1959_1543194.pkl
7680
processsing summary_bill_1959_1542898.pkl
14592
processsing summary_bill_1959_1543293.pkl
16896
processsing summary_bill_1959_1546438.pkl
7680
processsing summary_bill_1811_1403806.pkl
28416
processsing summary_bill_1811_1393218.pkl
9216
processsing summary_bill_1959_1543455.pkl
7680
processsing summary_bill_1959_1543430.pkl
13824
processsing summary_bill_1959_1546201.pkl
6912
processsing summary_bill_1959_1545793.pkl
15360


/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize i

14592
processsing summary_bill_1959_1543042.pkl
11520
processsing summary_bill_1959_1545796.pkl
10752
processsing summary_bill_1959_1542673.pkl
10752
processsing summary_bill_1811_1403563.pkl
13056
processsing summary_bill_1959_1543001.pkl
20736
processsing summary_bill_1959_1546034.pkl
9984
processsing summary_bill_1959_1543462.pkl
21504
processsing summary_bill_1811_1393021.pkl
25344
processsing summary_bill_1959_1542689.pkl
12288
processsing summary_bill_1959_1543505.pkl
15360
processsing summary_bill_1959_1542735.pkl
27648
processsing summary_bill_1811_1406434.pkl
6144
processsing summary_bill_1811_1430830.pkl
16128
processsing summary_bill_1811_1406849.pkl
18432
processsing summary_bill_1811_1393154.pkl
12288
processsing summary_bill_1811_1395601.pkl
12288
processsing summary_bill_1959_1543478.pkl
13824
processsing summary_bill_1811_1403550.pkl
9984
processsing summary_bill_1811_1405709.pkl
8448
processsing summary_bill_1959_1543091.pkl
9216
processsing summary_bill_1811_1396545.p

/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize i

processsing summary_bill_1811_1395476.pkl
10752
processsing summary_bill_1959_1543126.pkl
13824
processsing summary_bill_1811_1506887.pkl
23040
processsing summary_bill_1959_1543397.pkl
12288
processsing summary_bill_1959_1543521.pkl
10752
processsing summary_bill_1959_1543174.pkl
8448
processsing summary_bill_1811_1396528.pkl
8448
processsing summary_bill_1811_1405712.pkl
8448
processsing summary_bill_1959_1542761.pkl
9216
processsing summary_bill_1959_1543409.pkl
9216
processsing summary_bill_1959_1543375.pkl
8448
processsing summary_bill_1811_1400144.pkl
22272
processsing summary_bill_1811_1393087.pkl
11520
processsing summary_bill_1811_1393078.pkl
16896
processsing summary_bill_1811_1493138.pkl
7680
processsing summary_bill_1959_1544144.pkl
18432
processsing summary_bill_1959_1543415.pkl
23040
processsing summary_bill_1811_1396548.pkl
12288
processsing summary_bill_1959_1543249.pkl
9984
processsing summary_bill_1811_1396596.pkl
19968
processsing summary_bill_1959_1546136.pkl
15360


...

/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize i

12288
processsing summary_bill_1959_1545965.pkl
10752
processsing summary_bill_1959_1543382.pkl
6912
processsing summary_bill_1959_1542963.pkl
19200
processsing summary_bill_1811_1403544.pkl
16128
processsing summary_bill_1811_1393145.pkl
12288
processsing summary_bill_1959_1543492.pkl
21504
processsing summary_bill_1959_1545969.pkl
17664
processsing summary_bill_1959_1543506.pkl
19200
processsing summary_bill_1959_1543309.pkl
32256
processsing summary_bill_1959_1543473.pkl
9984
processsing summary_bill_1811_1396656.pkl
19200
processsing summary_bill_1959_1543239.pkl
8448
processsing summary_bill_1811_1396643.pkl
9216
processsing summary_bill_1959_1546468.pkl
10752
processsing summary_bill_1811_1393131.pkl
16128
processsing summary_bill_1959_1542821.pkl
13824
processsing summary_bill_1959_1544159.pkl
22272
processsing summary_bill_1959_1543328.pkl
16128
processsing summary_bill_1811_1430840.pkl
6144
processsing summary_bill_1811_1392994.pkl
7680
processsing summary_bill_1811_1393019.pk

/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize i

processsing summary_bill_1811_1399788.pkl
14592
processsing summary_bill_1811_1393184.pkl
8448
processsing summary_bill_1959_1546143.pkl
10752
processsing summary_bill_1959_1544161.pkl
9216
processsing summary_bill_1959_1543380.pkl
17664
processsing summary_bill_1959_1543369.pkl
6144
processsing summary_bill_1811_1398371.pkl
11520
processsing summary_bill_1811_1396608.pkl
16128
processsing summary_bill_1959_1545866.pkl
7680
processsing summary_bill_1811_1396492.pkl
10752
processsing summary_bill_1811_1435209.pkl
13824
processsing summary_bill_1811_1395471.pkl
11520
processsing summary_bill_1959_1542901.pkl
9216
processsing summary_bill_1811_1399899.pkl
18432
processsing summary_bill_1811_1396097.pkl
13056
processsing summary_bill_1811_1403844.pkl
9984


/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/home/bhersh/git-projects/github/nlp_legislation_prediction/venv/lib/python3.8/site-packages/torch/_tensor.py:493: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
